# Setup

In [28]:
# was needed to download files from repo

# Download TorchVision repo to use some files from
# references/detection
# !git clone https://github.com/pytorch/vision.git
# !cd vision
# !git checkout v0.3.0

# !cp references/detection/utils.py ../
# !cp references/detection/transforms.py ../
# !cp references/detection/coco_eval.py ../
# !cp references/detection/engine.py ../
# !cp references/detection/coco_utils.py ../

# Imports

In [9]:
import fiftyone as fo
import fiftyone.utils.coco as fouc
from fiftyone.core.labels import Detection
from PIL import Image

import torch
import torch.nn as nn
import torch.utils
import torch.utils.data

import torchvision
from torchvision.models.segmentation import fcn_resnet50, FCN_ResNet50_Weights
from torchvision.models.detection.mask_rcnn import maskrcnn_resnet50_fpn, MaskRCNNPredictor
from torchvision.models.detection import MaskRCNN_ResNet50_FPN_Weights
from torchvision.models.detection.faster_rcnn import FastRCNNPredictor

import matplotlib.pyplot as plt
import numpy as np

import os
import importlib
import sys
from pathlib import Path
from datetime import datetime

import utils
import train
from train import train_one_epoch, evaluate
import transforms as T

here = os.getcwd()
sys.path.append(os.path.join(here, '..'))
import DatasetLoaders
importlib.reload(DatasetLoaders)
from DatasetLoaders import HRSIDSegmentationDataset


In [46]:
importlib.reload(utils)
importlib.reload(T)
importlib.reload(train)
importlib.reload(fo)
importlib.reload(fouc)


<module 'fiftyone.utils.coco' from '/home/k3vinli/miniconda3/envs/torch-38/lib/python3.10/site-packages/fiftyone/utils/coco.py'>

# loading data into fiftyone

In [31]:
p = Path()
top_dir = p.absolute().parents[1]
top_dir

PosixPath('/home/k3vinli/ENEE439/Capstone')

In [11]:
# Loading Dataset
name = "HRSID"
if name in fo.list_datasets():
    dataset_traintest = fo.load_dataset(name)
else:
    dataset_dir = top_dir / "Datasets" / "HRSID"
    # The type of the dataset being imported
    dataset_type = fo.types.COCODetectionDataset

    dataset_traintest = fo.Dataset.from_dir(
        dataset_dir=dataset_dir,
        dataset_type=dataset_type,
        name=name,
    )

In [33]:
# dataset_traintest.delete()

In [12]:
name = "HRSID_train"
if name in fo.list_datasets():
    dataset_train = fo.load_dataset(name)
else:
    dataset_dir = top_dir / "Datasets" / "HRSID"
    label_path = top_dir / "Datasets"/ "HRSID" / "annotations" / "train2017.json"
    # The type of the dataset being imported
    dataset_type = fo.types.COCODetectionDataset

    dataset_train = fo.Dataset.from_dir(
        dataset_dir=dataset_dir,
        dataset_type=dataset_type,
        name=name,
        labels_path=label_path
    )

In [35]:
# dataset_train.delete()

In [13]:
name = "HRSID_test"
if name in fo.list_datasets():
    dataset_test = fo.load_dataset(name)
else:
    dataset_dir = top_dir / "Datasets" / "HRSID"
    label_path = top_dir / "Datasets"/ "HRSID" / "annotations" / "test2017.json"
    # The type of the dataset being imported
    dataset_type = fo.types.COCODetectionDataset

    dataset_test = fo.Dataset.from_dir(
        dataset_dir=dataset_dir,
        dataset_type=dataset_type,
        name=name,
        labels_path=label_path
    )

In [14]:
dataset_train.compute_metadata()
dataset_test.compute_metadata()

# explore fiftyone useage

In [38]:
paths = dataset_train.values("filepath")
sample = dataset_train[paths[1]]
sample.metadata

<ImageMetadata: {
    'size_bytes': None,
    'mime_type': None,
    'width': 800,
    'height': 800,
    'num_channels': None,
}>

In [39]:
#sample

In [40]:
img = Image.open(paths[1]).convert("RGB")
detections = sample["detections"].detections
segmentations = sample["segmentations"].detections

In [41]:
classes = dataset_train.distinct("%s.detections.label" % "segmentations")

In [42]:
# segmentations

In [43]:
labels_map_rev = {c: i for i, c in enumerate(classes)}
labels_map_rev


{'ship': 0}

In [44]:
for det in segmentations:
    category_id=labels_map_rev[det.label]
    coco_obj=fouc.COCOObject.from_label(det, sample.metadata, category_id=category_id)
    x,y,w,h=coco_obj.bbox

In [45]:
# [coco_obj.segmentation], dtype=torch.float

In [46]:
sample = dataset_test.first()
frame_size = (sample.metadata["width"], sample.metadata["height"])
detection = sample["segmentations"]["detections"][0]

segmentation = detection.to_segmentation(frame_size=frame_size)
full_img_mask = segmentation.mask
print(type(detection))
print("frame size", frame_size)
print("detection:", detection)
print("segmentation:", segmentation)
print("full img", full_img_mask.max())

<class 'fiftyone.core.labels.Detection'>
frame size (800, 800)
detection: <Detection: {
    'id': '645526021951373c4285f5de',
    'attributes': {},
    'tags': [],
    'label': 'ship',
    'bounding_box': [0.29625, 0.09875, 0.0525, 0.01],
    'mask': array([[False, False, False, False, False, False, False, False, False,
            False, False, False, False, False, False, False,  True,  True,
             True,  True,  True,  True,  True,  True,  True,  True,  True,
             True,  True,  True,  True,  True,  True,  True,  True,  True,
             True,  True, False, False, False, False],
           [False,  True,  True,  True,  True,  True,  True,  True,  True,
             True,  True,  True,  True,  True,  True,  True,  True,  True,
             True,  True,  True,  True,  True,  True,  True,  True,  True,
             True,  True,  True,  True,  True,  True,  True,  True,  True,
             True,  True,  True,  True,  True, False],
           [ True,  True,  True,  True,  Tr

In [15]:
session = fo.launch_app()

# Training MaskRCNN Model

In [19]:
def get_model(num_classes, pretrained=True):
    if pretrained:
        weights = MaskRCNN_ResNet50_FPN_Weights.DEFAULT
    else:
        weights = None
    model = maskrcnn_resnet50_fpn(weights=weights)

    # get number of input features for the classifier
    in_features = model.roi_heads.box_predictor.cls_score.in_features
    # replace the pre-trained head with a new one
    model.roi_heads.box_predictor = FastRCNNPredictor(in_features, num_classes)

    # now get the number of input features for the mask classifier
    in_features_mask = model.roi_heads.mask_predictor.conv5_mask.in_channels
    hidden_layer = 256
    # and replace the mask predictor with a new one
    model.roi_heads.mask_predictor = MaskRCNNPredictor(in_features_mask,
                                                       hidden_layer,
                                                       num_classes)

    return model

In [23]:
def get_transform():
    transforms = []
    transforms.append(T.PILToTensor())
    transforms.append(T.ConvertImageDtype(torch.float))
    
    return T.Compose(transforms)

In [121]:
def do_training(model, torch_dataset, torch_dataset_test, num_epochs=4, print_freq=10):
    data_loader = torch.utils.data.DataLoader(
        torch_dataset, batch_size=4, shuffle=False, num_workers=8,
        collate_fn=utils.collate_fn
    )
    data_loader_test = torch.utils.data.DataLoader(
        torch_dataset_test, batch_size=2, shuffle=False, num_workers=8,
        collate_fn=utils.collate_fn
    )

    device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
    print(f"Using {device}")
    model.to(device)

    params = [p for p in model.parameters() if p.requires_grad]
    optimizer = torch.optim.SGD(params, lr=0.005,
                                momentum=0.5, weight_decay=0.0005)

    lr_scheduler = torch.optim.lr_scheduler.StepLR(optimizer,
                                                    step_size=20,
                                                    gamma=0.1)
    for epoch in range(num_epochs):
        train_one_epoch(model=model,
                        optimizer=optimizer, 
                        data_loader=data_loader,
                        device=device, 
                        epoch=epoch, 
                        print_freq=print_freq)
        torch.nn.utils.clip_grad_norm_(model.parameters(), 1)
        lr_scheduler.step()
        evaluate(model=model, data_loader=data_loader_test, device=device)

In [24]:
HRSID_train = HRSIDSegmentationDataset(dataset_train, transforms=get_transform())
HRSID_test = HRSIDSegmentationDataset(dataset_test, transforms=get_transform())

In [52]:
x = np.array([0,0,0,255,255,0,0,0])
np.clip(x, 0, 1)

array([0, 0, 0, 1, 1, 0, 0, 0])

In [59]:
model = get_model(2)

In [60]:
do_training(model, HRSID_train, HRSID_test, num_epochs=20)


Using cuda
Epoch: [0]  [  0/911]  eta: 0:59:40  lr: 0.000002  loss: 5.1333 (5.1333)  loss_classifier: 0.5706 (0.5706)  loss_box_reg: 0.0896 (0.0896)  loss_mask: 2.2855 (2.2855)  loss_objectness: 1.9364 (1.9364)  loss_rpn_box_reg: 0.2512 (0.2512)  time: 3.9298  data: 3.4212  max mem: 4254
Epoch: [0]  [ 10/911]  eta: 0:11:59  lr: 0.000013  loss: 2.8339 (3.1338)  loss_classifier: 0.5309 (0.5410)  loss_box_reg: 0.1633 (0.1509)  loss_mask: 1.7565 (1.7786)  loss_objectness: 0.2123 (0.5874)  loss_rpn_box_reg: 0.0288 (0.0760)  time: 0.7989  data: 0.3470  max mem: 4437
Epoch: [0]  [ 20/911]  eta: 0:09:21  lr: 0.000024  loss: 2.7271 (3.2279)  loss_classifier: 0.5216 (0.5244)  loss_box_reg: 0.1254 (0.1370)  loss_mask: 1.6735 (1.7578)  loss_objectness: 0.1401 (0.7259)  loss_rpn_box_reg: 0.0264 (0.0829)  time: 0.4648  data: 0.0264  max mem: 4457
Epoch: [0]  [ 30/911]  eta: 0:08:24  lr: 0.000035  loss: 2.3342 (2.9703)  loss_classifier: 0.4812 (0.4997)  loss_box_reg: 0.1264 (0.1417)  loss_mask: 1.586

In [61]:
model_not_pretrained = get_model(2, False)

Downloading: "https://download.pytorch.org/models/resnet50-0676ba61.pth" to /home/k3vinli/.cache/torch/hub/checkpoints/resnet50-0676ba61.pth
23.8%IOPub message rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_msg_rate_limit`.

Current values:
NotebookApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
NotebookApp.rate_limit_window=3.0 (secs)

53.8%IOPub message rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_msg_rate_limit`.

Current values:
NotebookApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
NotebookApp.rate_limit_window=3.0 (secs)

83.4%IOPub message rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.io

In [62]:
do_training(model_not_pretrained, HRSID_train, HRSID_test, num_epochs=20)


Using cuda
Epoch: [0]  [  0/911]  eta: 1:08:48  lr: 0.000002  loss: 5.5138 (5.5138)  loss_classifier: 0.6979 (0.6979)  loss_box_reg: 0.0104 (0.0104)  loss_mask: 3.6724 (3.6724)  loss_objectness: 0.6959 (0.6959)  loss_rpn_box_reg: 0.4372 (0.4372)  time: 4.5324  data: 3.9458  max mem: 5719
Epoch: [0]  [ 10/911]  eta: 0:14:10  lr: 0.000013  loss: 7.0853 (6.7667)  loss_classifier: 0.7142 (0.7121)  loss_box_reg: 0.0334 (0.0312)  loss_mask: 5.6600 (5.1877)  loss_objectness: 0.6929 (0.6932)  loss_rpn_box_reg: 0.0756 (0.1426)  time: 0.9437  data: 0.3664  max mem: 5719
Epoch: [0]  [ 20/911]  eta: 0:11:00  lr: 0.000024  loss: 5.3873 (5.5885)  loss_classifier: 0.7104 (0.7100)  loss_box_reg: 0.0227 (0.0266)  loss_mask: 3.8680 (3.9986)  loss_objectness: 0.6932 (0.6938)  loss_rpn_box_reg: 0.0427 (0.1595)  time: 0.5518  data: 0.0105  max mem: 5719
Epoch: [0]  [ 30/911]  eta: 0:09:52  lr: 0.000035  loss: 3.5871 (4.8495)  loss_classifier: 0.6994 (0.7054)  loss_box_reg: 0.0183 (0.0255)  loss_mask: 2.045

In [94]:
img_paths = dataset_traintest.values("filepath")
img1 = Image.open(img_paths[2]).convert("RGB")

piltotensor = torchvision.transforms.PILToTensor()
convertdtype = torchvision.transforms.ConvertImageDtype(torch.float32)
img1_tensor = piltotensor(img1)
img1_tensor = convertdtype(img1_tensor)
img1_tensor = img1_tensor.reshape((-1, 3, 800, 800))
img1_tensor.shape

torch.Size([1, 3, 800, 800])

In [102]:
model.eval()
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
preds = model(img1_tensor.to(device))
preds[0]["masks"].shape


torch.Size([12, 1, 800, 800])

In [64]:
file_name_default = f"maskrcnn_default_e20_lr001_m5.pt"
file_name_random = f"maskrcnn_random_e20_lr001_m5.pt"

In [66]:
# https://pytorch.org/tutorials/beginner/saving_loading_models.html
# Saving Model
torch.save(model.state_dict(), os.path.abspath(f"maskrcnn_weights/{file_name_default}"))
torch.save(model_not_pretrained.state_dict(), os.path.abspath(f"maskrcnn_weights/{file_name_random}"))

In [48]:
def convert_torch_predictions(preds, det_id, s_id, w, h, classes):
    # Convert the outputs of the torch model into a FiftyOne Detections object
    dets = []
    for bbox, label, score, masks in zip(
        preds["boxes"].cpu().detach().numpy(), 
        preds["labels"].cpu().detach().numpy(), 
        preds["scores"].cpu().detach().numpy(),
        preds["masks"].cpu().detach().numpy()
    ):
        # Parse prediction into FiftyOne Detection object
        x0,y0,x1,y1 = bbox
        coco_obj = fouc.COCOObject(det_id, s_id, int(label), [x0, y0, x1-x0, y1-y0], segmentation=masks[0].tolist())
        det = coco_obj.to_detection((w,h), classes, load_segmentation=True)
        det["confidence"] = float(score)
        dets.append(det)
        det_id += 1
        
    detections = fo.Detections(detections=dets)
        
    return detections, det_id

In [49]:
def add_detections(model, torch_dataset, view, field_name="predictions"):
    # Run inference on a dataset and add results to FiftyOne
    torch.set_num_threads(1)
    device = torch.device('cuda') if torch.cuda.is_available() else torch.device('cpu')
    print("Using device %s" % device)

    model.eval()
    model.to(device)
    image_paths = torch_dataset.img_paths
    classes = torch_dataset.classes
    det_id = 0
    
    with fo.ProgressBar() as pb:
        for img, targets in pb(torch_dataset):
            # Get FiftyOne sample indexed by unique image filepath
            img_id = int(targets["image_id"][0])
            img_path = image_paths[img_id]
            sample = view[img_path]
            s_id = sample.id
            w = sample.metadata["width"]
            h = sample.metadata["height"]
            
            # Inference
            preds = model(img.unsqueeze(0).to(device))[0]
            
            detections, det_id = convert_torch_predictions(
                preds, 
                det_id, 
                s_id, 
                w, 
                h, 
                classes,
            )
            
            sample[field_name] = detections
            sample.save()

In [108]:
add_detections(model, HRSID_test, dataset_traintest, field_name="predictions")

Using device cuda
 100% |███████████████| 1961/1961 [11.7m elapsed, 0s remaining, 6.0 samples/s]      


In [109]:
results = fo.evaluate_detections(
    dataset_traintest, 
    "predictions", 
    classes=["ship"],
    eval_key="eval", 
    compute_mAP=True,
    gt_field='detections'
)

Evaluating detections...
 100% |███████████████| 5604/5604 [1.1m elapsed, 0s remaining, 125.5 samples/s]       
Performing IoU sweep...
 100% |███████████████| 5604/5604 [27.3s elapsed, 0s remaining, 208.8 samples/s]      


In [110]:
results.mAP()

0.20103878476183756

In [111]:
results.print_report()

              precision    recall  f1-score   support

        ship       0.28      0.31      0.29     16951

   micro avg       0.28      0.31      0.29     16951
   macro avg       0.28      0.31      0.29     16951
weighted avg       0.28      0.31      0.29     16951



In [114]:
results = fo.evaluate_detections(
    dataset_traintest, 
    "segmentations", 
    classes=["ship"],
    eval_key="eval_seg", 
    compute_mAP=True,
    gt_field='detections'
)

Evaluating detections...
 100% |███████████████| 5604/5604 [59.4s elapsed, 0s remaining, 149.0 samples/s]      
Performing IoU sweep...
 100% |███████████████| 5604/5604 [38.4s elapsed, 0s remaining, 177.5 samples/s]      


ValueError: All predicted objects must have their `confidence` attribute populated in order to compute precision-recall curves

In [ ]:
session.view = dataset_traintest.sort_by("eval_fp", reverse=True)

In [116]:
# training again
model.eval()

MaskRCNN(
  (transform): GeneralizedRCNNTransform(
      Normalize(mean=[0.485, 0.456, 0.406], std=[0.229, 0.224, 0.225])
      Resize(min_size=(800,), max_size=1333, mode='bilinear')
  )
  (backbone): BackboneWithFPN(
    (body): IntermediateLayerGetter(
      (conv1): Conv2d(3, 64, kernel_size=(7, 7), stride=(2, 2), padding=(3, 3), bias=False)
      (bn1): FrozenBatchNorm2d(64, eps=0.0)
      (relu): ReLU(inplace=True)
      (maxpool): MaxPool2d(kernel_size=3, stride=2, padding=1, dilation=1, ceil_mode=False)
      (layer1): Sequential(
        (0): Bottleneck(
          (conv1): Conv2d(64, 64, kernel_size=(1, 1), stride=(1, 1), bias=False)
          (bn1): FrozenBatchNorm2d(64, eps=0.0)
          (conv2): Conv2d(64, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
          (bn2): FrozenBatchNorm2d(64, eps=0.0)
          (conv3): Conv2d(64, 256, kernel_size=(1, 1), stride=(1, 1), bias=False)
          (bn3): FrozenBatchNorm2d(256, eps=0.0)
          (relu): ReLU(in

In [118]:
do_training(model, HRSID_train, HRSID_test, num_epochs=20)


Using cuda
Epoch: [0]  [  0/911]  eta: 1:28:54  lr: 0.000010  loss: 0.6803 (0.6803)  loss_classifier: 0.0933 (0.0933)  loss_box_reg: 0.1507 (0.1507)  loss_mask: 0.2653 (0.2653)  loss_objectness: 0.0349 (0.0349)  loss_rpn_box_reg: 0.1360 (0.1360)  time: 5.8558  data: 4.5149  max mem: 5719
Epoch: [0]  [ 10/911]  eta: 0:20:10  lr: 0.000065  loss: 0.2178 (0.3120)  loss_classifier: 0.0194 (0.0333)  loss_box_reg: 0.0513 (0.0730)  loss_mask: 0.1344 (0.1607)  loss_objectness: 0.0018 (0.0106)  loss_rpn_box_reg: 0.0076 (0.0345)  time: 1.3431  data: 0.4182  max mem: 5719
Epoch: [0]  [ 20/911]  eta: 0:16:14  lr: 0.000120  loss: 0.2016 (0.3132)  loss_classifier: 0.0179 (0.0359)  loss_box_reg: 0.0474 (0.0715)  loss_mask: 0.1327 (0.1596)  loss_objectness: 0.0012 (0.0111)  loss_rpn_box_reg: 0.0036 (0.0352)  time: 0.8557  data: 0.0106  max mem: 5719
Epoch: [0]  [ 30/911]  eta: 0:14:34  lr: 0.000175  loss: 0.1866 (0.2977)  loss_classifier: 0.0165 (0.0344)  loss_box_reg: 0.0356 (0.0667)  loss_mask: 0.132

In [119]:
file_name_retrain = f"maskrcnn_retrain_e20_lr005_m5.pt"


In [120]:
torch.save(model.state_dict(), os.path.abspath(f"maskrcnn_weights/{file_name_retrain}"))

In [123]:
do_training(model, HRSID_train, HRSID_test, num_epochs=100)


Using cuda
Epoch: [0]  [  0/911]  eta: 1:04:47  lr: 0.000010  loss: 0.5622 (0.5622)  loss_classifier: 0.0625 (0.0625)  loss_box_reg: 0.1275 (0.1275)  loss_mask: 0.2344 (0.2344)  loss_objectness: 0.0134 (0.0134)  loss_rpn_box_reg: 0.1244 (0.1244)  time: 4.2670  data: 3.7176  max mem: 6307
Epoch: [0]  [ 10/911]  eta: 0:13:08  lr: 0.000065  loss: 0.1875 (0.2563)  loss_classifier: 0.0214 (0.0274)  loss_box_reg: 0.0433 (0.0577)  loss_mask: 0.1249 (0.1443)  loss_objectness: 0.0016 (0.0037)  loss_rpn_box_reg: 0.0051 (0.0232)  time: 0.8746  data: 0.3442  max mem: 6307
Epoch: [0]  [ 20/911]  eta: 0:10:48  lr: 0.000120  loss: 0.1805 (0.2626)  loss_classifier: 0.0201 (0.0279)  loss_box_reg: 0.0391 (0.0594)  loss_mask: 0.1202 (0.1453)  loss_objectness: 0.0016 (0.0046)  loss_rpn_box_reg: 0.0027 (0.0254)  time: 0.5506  data: 0.0096  max mem: 6307
Epoch: [0]  [ 30/911]  eta: 0:10:05  lr: 0.000175  loss: 0.1623 (0.2491)  loss_classifier: 0.0159 (0.0263)  loss_box_reg: 0.0316 (0.0556)  loss_mask: 0.120

In [181]:
file_name_retrain_100 = f"maskrcnn_retrain_e100_lr005_m5.pt"


In [182]:
torch.save(model.state_dict(), os.path.abspath(f"maskrcnn_weights/{file_name_retrain_100}"))

In [161]:
# dataset_traintest.delete_sample_field("predictions")

In [165]:
add_detections(model, HRSID_test, dataset_traintest, field_name="predictions")

Using device cuda
 100% |███████████████| 1961/1961 [12.3m elapsed, 0s remaining, 5.2 samples/s]      


In [167]:
dataset_traintest

Name:        HRSID
Media type:  image
Num samples: 5604
Persistent:  False
Tags:        []
Sample fields:
    id:            fiftyone.core.fields.ObjectIdField
    filepath:      fiftyone.core.fields.StringField
    tags:          fiftyone.core.fields.ListField(fiftyone.core.fields.StringField)
    metadata:      fiftyone.core.fields.EmbeddedDocumentField(fiftyone.core.metadata.ImageMetadata)
    detections:    fiftyone.core.fields.EmbeddedDocumentField(fiftyone.core.labels.Detections)
    segmentations: fiftyone.core.fields.EmbeddedDocumentField(fiftyone.core.labels.Detections)
    eval_tp:       fiftyone.core.fields.IntField
    eval_fp:       fiftyone.core.fields.IntField
    eval_fn:       fiftyone.core.fields.IntField
    predictions:   fiftyone.core.fields.EmbeddedDocumentField(fiftyone.core.labels.Detections)

In [158]:
img_paths[0]

'/home/k3vinli/ENEE439/Capstone/Datasets/HRSID/data/P0001_0_800_10190_10990.jpg'

In [171]:
img_paths = dataset_traintest.values("filepath")
sample = dataset_traintest[img_paths[0]]
sample

<Sample: {
    'id': '645525cc1951373c4284f704',
    'media_type': 'image',
    'filepath': '/home/k3vinli/ENEE439/Capstone/Datasets/HRSID/data/P0001_0_800_10190_10990.jpg',
    'tags': [],
    'metadata': <ImageMetadata: {
        'size_bytes': None,
        'mime_type': None,
        'width': 800,
        'height': 800,
        'num_channels': None,
    }>,
    'detections': <Detections: {
        'detections': [
            <Detection: {
                'id': '645525cc1951373c4284f700',
                'attributes': {},
                'tags': [],
                'label': 'ship',
                'bounding_box': [0.29625, 0.09875, 0.0525, 0.01],
                'mask': None,
                'confidence': None,
                'index': None,
                'iscrowd': 0,
                'eval_seg': 'tp',
                'eval_seg_id': '645525cc1951373c4284f702',
                'eval_seg_iou': 0.9999999999999988,
                'eval': 'fn',
                'eval_id': '',
           

In [168]:
results = fo.evaluate_detections(
    dataset_traintest, 
    "predictions", 
    classes=["ship"],
    eval_key="eval", 
    compute_mAP=True,
    gt_field='detections'
)

Evaluating detections...
 100% |███████████████| 5604/5604 [41.9s elapsed, 0s remaining, 186.7 samples/s]      
Performing IoU sweep...
 100% |███████████████| 5604/5604 [25.7s elapsed, 0s remaining, 227.8 samples/s]      


In [169]:
results.mAP()

0.22475910980593988

In [179]:
results.report()

{'ship': {'precision': 0.4289761230271145,
  'recall': 0.3126659194147838,
  'f1-score': 0.3617006756295639,
  'support': 16951},
 'micro avg': {'precision': 0.4289761230271145,
  'recall': 0.3126659194147838,
  'f1-score': 0.3617006756295639,
  'support': 16951},
 'macro avg': {'precision': 0.4289761230271145,
  'recall': 0.3126659194147838,
  'f1-score': 0.3617006756295639,
  'support': 16951},
 'weighted avg': {'precision': 0.4289761230271145,
  'recall': 0.3126659194147838,
  'f1-score': 0.3617006756295639,
  'support': 16951}}

In [170]:
results.print_report()

              precision    recall  f1-score   support

        ship       0.43      0.31      0.36     16951

   micro avg       0.43      0.31      0.36     16951
   macro avg       0.43      0.31      0.36     16951
weighted avg       0.43      0.31      0.36     16951



In [157]:
dataset_traintest

Name:        HRSID
Media type:  image
Num samples: 5604
Persistent:  False
Tags:        []
Sample fields:
    id:            fiftyone.core.fields.ObjectIdField
    filepath:      fiftyone.core.fields.StringField
    tags:          fiftyone.core.fields.ListField(fiftyone.core.fields.StringField)
    metadata:      fiftyone.core.fields.EmbeddedDocumentField(fiftyone.core.metadata.ImageMetadata)
    detections:    fiftyone.core.fields.EmbeddedDocumentField(fiftyone.core.labels.Detections)
    segmentations: fiftyone.core.fields.EmbeddedDocumentField(fiftyone.core.labels.Detections)
    predictions:   fiftyone.core.fields.EmbeddedDocumentField(fiftyone.core.labels.Detections)
    eval_tp:       fiftyone.core.fields.IntField
    eval_fp:       fiftyone.core.fields.IntField
    eval_fn:       fiftyone.core.fields.IntField

In [156]:
results = fo.evaluate_segmentations(
    dataset_traintest, 
    "predictions", 
    eval_key="eval_seg", 
    compute_mAP=True,
    gt_field='segmentations'
)

ValueError: Sample field 'predictions' is not a [<class 'fiftyone.core.labels.Segmentation'>] instance; found <class 'fiftyone.core.labels.Detections'>

In [ ]:
session.view = dataset_traintest.sort_by("eval_fp", reverse=True)

# Loading Previously Saved Model

In [20]:
PATH = "maskrcnn_weights/maskrcnn_retrain_e100_lr005_m5.pt"
model = get_model(2, False)
model.load_state_dict(torch.load(PATH))
model.eval()

MaskRCNN(
  (transform): GeneralizedRCNNTransform(
      Normalize(mean=[0.485, 0.456, 0.406], std=[0.229, 0.224, 0.225])
      Resize(min_size=(800,), max_size=1333, mode='bilinear')
  )
  (backbone): BackboneWithFPN(
    (body): IntermediateLayerGetter(
      (conv1): Conv2d(3, 64, kernel_size=(7, 7), stride=(2, 2), padding=(3, 3), bias=False)
      (bn1): FrozenBatchNorm2d(64, eps=1e-05)
      (relu): ReLU(inplace=True)
      (maxpool): MaxPool2d(kernel_size=3, stride=2, padding=1, dilation=1, ceil_mode=False)
      (layer1): Sequential(
        (0): Bottleneck(
          (conv1): Conv2d(64, 64, kernel_size=(1, 1), stride=(1, 1), bias=False)
          (bn1): FrozenBatchNorm2d(64, eps=1e-05)
          (conv2): Conv2d(64, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
          (bn2): FrozenBatchNorm2d(64, eps=1e-05)
          (conv3): Conv2d(64, 256, kernel_size=(1, 1), stride=(1, 1), bias=False)
          (bn3): FrozenBatchNorm2d(256, eps=1e-05)
          (relu):

In [50]:
add_detections(model, HRSID_test, dataset_test, field_name="predictions")

Using device cuda
 100% |███████████████| 1961/1961 [19.0m elapsed, 0s remaining, 2.7 samples/s]      


In [51]:
results = fo.evaluate_detections(
    dataset_test, 
    "predictions", 
    classes=["ship"],
    eval_key="eval", 
    compute_mAP=True,
    gt_field='detections'
)

Evaluating detections...
 100% |███████████████| 1961/1961 [24.3s elapsed, 0s remaining, 101.1 samples/s]      
Performing IoU sweep...
 100% |███████████████| 1961/1961 [17.9s elapsed, 0s remaining, 129.2 samples/s]      


In [52]:
results.mAP()

0.6347247628086541

In [53]:
results.print_report()

              precision    recall  f1-score   support

        ship       0.44      0.89      0.59      5921

   micro avg       0.44      0.89      0.59      5921
   macro avg       0.44      0.89      0.59      5921
weighted avg       0.44      0.89      0.59      5921



In [54]:
dataset_test

Name:        HRSID_test
Media type:  image
Num samples: 1961
Persistent:  False
Tags:        []
Sample fields:
    id:            fiftyone.core.fields.ObjectIdField
    filepath:      fiftyone.core.fields.StringField
    tags:          fiftyone.core.fields.ListField(fiftyone.core.fields.StringField)
    metadata:      fiftyone.core.fields.EmbeddedDocumentField(fiftyone.core.metadata.ImageMetadata)
    detections:    fiftyone.core.fields.EmbeddedDocumentField(fiftyone.core.labels.Detections)
    segmentations: fiftyone.core.fields.EmbeddedDocumentField(fiftyone.core.labels.Detections)
    predictions:   fiftyone.core.fields.EmbeddedDocumentField(fiftyone.core.labels.Detections)
    eval_tp:       fiftyone.core.fields.IntField
    eval_fp:       fiftyone.core.fields.IntField
    eval_fn:       fiftyone.core.fields.IntField

In [55]:
results_seg = fo.evaluate_segmentations(
    dataset_test,
    pred_field="predictions",
    classes=["ship"],
    eval_key="eval_seg",
    compute_mAP=True,
    gt_field='segmentations'
)

ValueError: Sample field 'predictions' is not a [<class 'fiftyone.core.labels.Segmentation'>] instance; found <class 'fiftyone.core.labels.Detections'>

In [38]:
a = np.array([0,1,1,0])
if a and True:
    print('hi')

ValueError: The truth value of an array with more than one element is ambiguous. Use a.any() or a.all()